# Random City Model
_Felix Haumann_

Prerequisites:
- Excel file with city map where Roads are marked with "X"
- Excel map needs to have one lot marked with "D" which is the depot

Model parameters:
- Every road accessible lot will have a house
- House have between 1 and 15 households
- Households are assigned to the houses at (insert probability here)
- Every household can potentially receive parcels
- Probability for a household is (insert probability here)
- The probability is calculated for each household within a house and the resulting parcels then summed up for that house

---
# SETUP

### Library imports

In [1]:
import random
import xlwings as xw
import pandas as pd
import numpy as np
from pathfinding.core.diagonal_movement import DiagonalMovement
from pathfinding.core.grid import Grid
from pathfinding.finder.a_star import AStarFinder
from sklearn.cluster import KMeans
from IPython.display import display
import string
from pprint import pprint
from helper import generate_letter_combinations, save_df_as_csv, read_df_from_csv

### Switches
rerun_simulation: decides whether the simulation will be run again or whether the available csv files will be used

In [2]:
rerun_simulation = True

### Paths

In [3]:
# Excel files
blank_wb_city = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\CITY_BLANK.xlsx"
blank_ws_city = "BLANK"

households_wb_city = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\CITY_HOUSEHOLDS.xlsx"
households_ws_city = "HOUSEHOLDS"
households_col_range = "C:CX"

quantity_wb_city = r"C:\Users\fhaum\OneDrive\401 MASTER - Masterarbeit\04 Kalkulationen\CITY_QTY.xlsx"
quantity_ws_city = "QTY"

# CSV filenames
# TODO: add check if csv files are all available
csv_name_map_base = "map_base"
csv_distance_matrix_base = "distance_matrix_district_"


### City parameters

In [4]:
# Defining the map boundaries from the Excel file
first_row = 3
first_col = 3
last_row = 102
last_col = 102
num_of_rows = last_row-first_row+1
num_of_cols = last_col-first_col+1
column_range = "C:CX"
skiprows = 1
map_char_street = "X"
map_char_depot = "D"
delivery_districts = {"A": [(0, 0), (33, 23)],
                      "B": [(34, 0), (71, 26)],
                      "C": [(72, 0), (99, 35)],
                      "D": [(0, 24), (34, 47)],
                      "E": [(35, 27), (71, 52)],
                      "F": [(72, 36), (99, 66)],
                      "G": [(0, 48), (34, 71)],
                      "H": [(35, 53), (71, 75)],
                      "I": [(72, 67), (99, 99)],
                      "J": [(0, 72), (34, 99)],
                      "K": [(35, 76), (71, 99)]
                      }

# Pathfinding variables
# These variables are assigned to the cells for pathfinding
# Tiles with val 1 = walkable
# Tiles with val >1 = walkable but higher cost
# Tiles with val 0 or negative = not walkable
# Note: the last tile (end_coordinates) must have a positive value otherwise it cant be reached
path_val_depot = 200
path_val_house = 500
path_val_house_with_parcels = 100
path_val_empty_lot = 0
path_val_road = 1

### Weights & distributions

In [5]:
# Parcel quantity choices and weights
parcel_quantity_choices = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
parcel_quantity_weights = [0.8996, 0.0634, 0.0233, 0.0085, 0.0031, 0.0011, 0.0004, 0.0001, 0.0001, 0.0001, 0.0001]

# Household size choices and weights
household_size_choices = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]
household_size_weights = [0.4, 0.35, 0.045, 0.04, 0.035, 0.03, 0.025, 0.02, 0.015, 0.01, 0.005, 0.0025, 0.0125, 0.005, 0.005]

---
# Helper functions

In [6]:
def read_excel_map_as_df(wb_path, ws_name, col_range, skiprows, number_of_rows, number_of_cols):
    col_names = list(range(number_of_cols))
    df = pd.read_excel(wb_path, sheet_name=ws_name, usecols=col_range, skiprows=skiprows, nrows=number_of_rows, names=col_names)
    return df

---
# Define central datastructure

In [7]:
master_dict = {}

key_xy = "xy"
key_lot_use = "lot_use"
key_path_finding_val = "path_finding_val"
key_households = "households"
key_parcels = "parcels"
key_delivery_district = "delivery_district"
# Final format will be: {"AAA":{"xy":(0,0), "lot_use":-2, "households":2, "parcels":4}, "AAB":{"xy":(1,0), "lot_use": 1, "households":0, "parcels":0}}

In [8]:
def populate_master_dict(height:int = 100, width:int = 100):
    letter_combinations = generate_letter_combinations()

    for y in range(width):
        for x in range(height):
            name = next(letter_combinations)
            master_dict[name] = {key_xy: (x, y), key_lot_use: None, key_households: 0, key_parcels: 0, key_delivery_district:"", key_path_finding_val:0}

populate_master_dict()

In [9]:
pprint(master_dict)

{'AAA': {'delivery_district': '',
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (0, 0)},
 'AAB': {'delivery_district': '',
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (1, 0)},
 'AAC': {'delivery_district': '',
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (2, 0)},
 'AAD': {'delivery_district': '',
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (3, 0)},
 'AAE': {'delivery_district': '',
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (4, 0)},
 'AAF': {'delivery_district': '',
         'households': 0,
         'lot_use': None,
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (5, 0)},
 'AAG': {'

---
# Prepare maps

### Base map from Excel

In [10]:
if rerun_simulation:
    map_base = read_excel_map_as_df(wb_path=blank_wb_city, ws_name=blank_ws_city, col_range=column_range,
                                    skiprows=skiprows, number_of_rows=num_of_rows, number_of_cols=num_of_cols)
    save_df_as_csv(map_base, csv_name_map_base)
else:
    map_base = read_df_from_csv(csv_name_map_base)

display(map_base)



0    1    2    3    4    5    6    7    8    9   ...   90   91   92   93   
0   NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN  \
1   NaN    D  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN   
2   NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN   
3   NaN    X    X    X    X    X    X    X    X    X  ...    X    X    X    X   
4   NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN    X  NaN  NaN   
..  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
95  NaN  NaN    X  NaN  NaN  NaN    X  NaN  NaN  NaN  ...    X  NaN  NaN  NaN   
96  NaN  NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...    X  NaN  NaN  NaN   
97    X    X    X    X    X    X    X    X    X    X  ...    X  NaN  NaN  NaN   
98  NaN  NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...  NaN  NaN  NaN  NaN   
99  NaN  NaN    X  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...    X    X    X    X   

     94   95   96   97   98   99  
0   NaN  NaN  NaN  NaN  NaN  NaN  
1   NaN  NaN  NaN  NaN  NaN  NaN  
2   NaN  NaN  NaN  NaN  NaN  NaN  
3     X    X    X    X    X    X  
4   NaN  NaN  NaN    X  NaN    X  
..  ...  ...  ...  ...  ...  ...  
95  NaN    X  NaN  NaN    X  NaN  
96  NaN    X  NaN  NaN    X  NaN  
97  NaN    X  NaN  NaN    X  NaN  
98  NaN    X  NaN  NaN    X  NaN  
99    X    X    X    X    X  NaN  

[100 rows x 100 columns]

### Copy base map

In [11]:
map_lot_use = map_base.copy()
map_lot_use = map_lot_use.fillna(0)  # Replace NaN with empty lots

In [12]:
map_parcel = map_base.copy()

In [13]:
map_pathfinding = map_base.copy()

### Map styling

In [14]:
def display_styled_map(map_to_style):
    center_style = [
        {'selector': 'td',
         'props': [('text-align', 'center')]}
    ]
    styled_map = map_to_style.style
    styled_map.set_table_styles(center_style)
    display(styled_map)

---
# Populate city with houses

In [15]:
def lot_next_to_road(map_df: pd.DataFrame, x:int, y:int, map_char_street) -> bool:
    """
    Checks if current lot is next to a road
    """
    own = map_df.iat[y, x]
    above = map_df.iat[y - 1, x] if y - 1 >= 0 else 0
    left = map_df.iat[y, x - 1] if y - 1 >= 0 else 0
    below = map_df.iat[y + 1, x] if y + 1 < map_df.shape[0] else 0
    right = map_df.iat[y, x + 1] if x + 1 < map_df.shape[1] else 0


    around = {"a": True if above == map_char_street else False,
              "l": True if left == map_char_street else False,
              "r": True if right == map_char_street else False,
              "b": True if below == map_char_street else False}
    any_surround = any(around.values())

    if own != map_char_street and any_surround:
        return True
    else:
        return False


In [16]:
def select_household_size():
    result = random.choices(household_size_choices, household_size_weights, k=1)
    res_int = result[0]
    return res_int

In [17]:
def select_parcel_quantity():
    result = random.choices(parcel_quantity_choices, parcel_quantity_weights, k=1)
    res_int = result[0]
    return res_int

In [50]:
def evaluate_lot_use(map_df: pd.DataFrame) -> list:
    """
    Evaluates every lot in the master_dict for it use.
    If a lot is by a road a house will be places, the households in the house chosen at random based on the choices and weights defined.
    The parcels each household receives which are again based in choices and weights are summed up for each house.
    The master_dict will be edited to incorporate the lot use for printing a pretty map.
    The coordinates of the depot or depots will be returned as list of tuples.
    :param map_df:
    :return: depot_coordinates
    """
    depot_coordinates = []
    for lot, info in master_dict.items():
        x, y = info[key_xy]
        cell_val = map_df.iat[y, x]
        if cell_val == 0:
            if lot_next_to_road(map_df, x, y, map_char_street):
                households_in_house = select_household_size()
                parcels_to_house = 0
                for household in range(households_in_house):
                    parcels_to_house += select_parcel_quantity()
                info[key_households] = households_in_house
                info[key_parcels] = parcels_to_house
                if parcels_to_house > 0:
                    info[key_lot_use] = "P"
                    info[key_path_finding_val] = path_val_house_with_parcels
                else:
                    info[key_lot_use] = "H"
                    info[key_path_finding_val] = path_val_house
            else:
                info[key_lot_use] = "."
        elif cell_val == map_char_depot:
            info[key_lot_use] = map_char_depot
            info[key_path_finding_val] = path_val_depot
            depot_coordinates.append(info[key_xy])
        elif cell_val == map_char_street:
            info[key_lot_use] = " "
            info[key_path_finding_val] = path_val_road
        else:
            info[key_lot_use] = "WTF"
    return depot_coordinates


In [54]:
depots_xy = evaluate_lot_use(map_lot_use)
display(map_lot_use)

0  1  2  3  4  5  6  7  8  9   ... 90 91 92 93 94 95 96 97 98 99
0   0  0  0  0  0  0  0  0  0  0  ...  0  0  0  0  0  0  0  0  0  0
1   0  D  0  0  0  0  0  0  0  0  ...  0  0  0  0  0  0  0  0  0  0
2   0  X  0  0  0  0  0  0  0  0  ...  0  0  0  0  0  0  0  0  0  0
3   0  X  X  X  X  X  X  X  X  X  ...  X  X  X  X  X  X  X  X  X  X
4   0  X  0  0  0  0  0  0  0  0  ...  0  X  0  0  0  0  0  X  0  X
.. .. .. .. .. .. .. .. .. .. ..  ... .. .. .. .. .. .. .. .. .. ..
95  0  0  X  0  0  0  X  0  0  0  ...  X  0  0  0  0  X  0  0  X  0
96  0  0  X  0  0  0  0  0  0  0  ...  X  0  0  0  0  X  0  0  X  0
97  X  X  X  X  X  X  X  X  X  X  ...  X  0  0  0  0  X  0  0  X  0
98  0  0  X  0  0  0  0  0  0  0  ...  0  0  0  0  0  X  0  0  X  0
99  0  0  X  0  0  0  0  0  0  0  ...  X  X  X  X  X  X  X  X  X  0

[100 rows x 100 columns]

In [20]:
pprint(master_dict)

{'AAA': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (0, 0)},
 'AAB': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (1, 0)},
 'AAC': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (2, 0)},
 'AAD': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (3, 0)},
 'AAE': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (4, 0)},
 'AAF': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (5, 0)},
 'AAG': {'delive

---
# Show parcel locations on map

In [21]:
def populate_parcel_map():
    for name, info in master_dict.items():
        x,y = info["xy"]
        lot_use = info["lot_use"]
        map_parcel.iat[y, x] = lot_use

In [22]:
populate_parcel_map()
display_styled_map(map_parcel)

---
# Setup pathfinding

#### Transform map for pathfinding

In [23]:
map_pathfinding = map_pathfinding.replace(map_char_street, -999)  # Replace 'X' values with -999 --> Road
map_pathfinding = map_pathfinding.replace(map_char_depot, -1000)  # Replace 'D' values with -1000 --> Depot
map_pathfinding = map_pathfinding.fillna(path_val_empty_lot) # Replace NaN values with -2 --> Empty lots
map_pathfinding = map_pathfinding.apply(pd.to_numeric, errors='coerce', downcast='integer')  # Transform float values to ints
map_pathfinding = map_pathfinding.mask(map_pathfinding >= 0, -1)  # Replace positive numeric values with -1
map_pathfinding = map_pathfinding.replace(-999, path_val_road)  # Replace -999 values with road_val
map_pathfinding = map_pathfinding.replace(-1000, path_val_depot)  # Replace -1000 values with depot_val

map_pathfinding

0    1   2   3   4   5   6   7   8   9   ...  90  91  92  93  94  95  96   
0   -1   -1  -1  -1  -1  -1  -1  -1  -1  -1  ...  -1  -1  -1  -1  -1  -1  -1  \
1   -1  200  -1  -1  -1  -1  -1  -1  -1  -1  ...  -1  -1  -1  -1  -1  -1  -1   
2   -1    1  -1  -1  -1  -1  -1  -1  -1  -1  ...  -1  -1  -1  -1  -1  -1  -1   
3   -1    1   1   1   1   1   1   1   1   1  ...   1   1   1   1   1   1   1   
4   -1    1  -1  -1  -1  -1  -1  -1  -1  -1  ...  -1   1  -1  -1  -1  -1  -1   
..  ..  ...  ..  ..  ..  ..  ..  ..  ..  ..  ...  ..  ..  ..  ..  ..  ..  ..   
95  -1   -1   1  -1  -1  -1   1  -1  -1  -1  ...   1  -1  -1  -1  -1   1  -1   
96  -1   -1   1  -1  -1  -1  -1  -1  -1  -1  ...   1  -1  -1  -1  -1   1  -1   
97   1    1   1   1   1   1   1   1   1   1  ...   1  -1  -1  -1  -1   1  -1   
98  -1   -1   1  -1  -1  -1  -1  -1  -1  -1  ...  -1  -1  -1  -1  -1   1  -1   
99  -1   -1   1  -1  -1  -1  -1  -1  -1  -1  ...   1   1   1   1   1   1   1   

    97  98  99  
0   -1  -1  -1  
1   -1  -1  -1  
2   -1  -1  -1  
3    1   1   1  
4    1  -1   1  
..  ..  ..  ..  
95  -1   1  -1  
96  -1   1  -1  
97  -1   1  -1  
98  -1   1  -1  
99   1   1  -1  

[100 rows x 100 columns]

### Populate pathfinding map with values from master_dict

In [24]:
def populate_pathfinding_map():
    for lot, info in master_dict.items():
        x, y = info[key_xy]
        path_value = info[key_path_finding_val]
        map_pathfinding.iat[y, x] = path_value

0    1    2    3    4    5    6    7    8    9   ...   90   91   92   93   
0     0    0    0    0    0    0    0    0    0  100  ...    0    0    0    0  \
1     0  200    0    0    0    0    0    0    0  500  ...    0    0    0    0   
2   500    1  500  500  500  500  100  500  500  500  ...  500  100  500  500   
3   100    1    1    1    1    1    1    1    1    1  ...    1    1    1    1   
4   500    1  100  500  500  500  500  500  500  100  ...  500    1  100  100   
..  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
95    0  500    1  500    0  100    1  500    0  500  ...    1  500  500  500   
96  100  500    1  500  500  500  500  500  500  500  ...    1  500    0    0   
97    1    1    1    1    1    1    1    1    1    1  ...    1  500    0    0   
98  500  100    1  500  500  500  500  500  500  100  ...  500  100  500  100   
99    0  100    1  100    0    0    0    0    0    0  ...    1    1    1    1   

     94   95   96   97   98   99  
0     0    0    0    0    0    0  
1     0    0    0    0    0    0  
2   500  500  500  500  500  500  
3     1    1    1    1    1    1  
4   500  500  100    1  100    1  
..  ...  ...  ...  ...  ...  ...  
95  500    1  500  500    1  500  
96  100    1  500  100    1  500  
97  500    1  100  500    1  500  
98  500    1  500  500    1  100  
99    1    1    1    1    1  500  

[100 rows x 100 columns]

(array([1], dtype=int64), array([1], dtype=int64))


In [25]:
populate_pathfinding_map()
display(map_pathfinding)

0    1    2    3    4    5    6    7    8    9   ...   90   91   92   93   
0     0    0    0    0    0    0    0    0    0  100  ...    0    0    0    0  \
1     0  200    0    0    0    0    0    0    0  500  ...    0    0    0    0   
2   500    1  500  500  500  500  100  500  500  500  ...  500  100  500  500   
3   100    1    1    1    1    1    1    1    1    1  ...    1    1    1    1   
4   500    1  100  500  500  500  500  500  500  100  ...  500    1  100  100   
..  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
95    0  500    1  500    0  100    1  500    0  500  ...    1  500  500  500   
96  100  500    1  500  500  500  500  500  500  500  ...    1  500    0    0   
97    1    1    1    1    1    1    1    1    1    1  ...    1  500    0    0   
98  500  100    1  500  500  500  500  500  500  100  ...  500  100  500  100   
99    0  100    1  100    0    0    0    0    0    0  ...    1    1    1    1   

     94   95   96   97   98   99  
0     0    0    0    0    0    0  
1     0    0    0    0    0    0  
2   500  500  500  500  500  500  
3     1    1    1    1    1    1  
4   500  500  100    1  100    1  
..  ...  ...  ...  ...  ...  ...  
95  500    1  500  500    1  500  
96  100    1  500  100    1  500  
97  500    1  100  500    1  500  
98  500    1  500  500    1  100  
99    1    1    1    1    1  500  

[100 rows x 100 columns]

In [26]:
def instantiate_grid(map_df: pd.DataFrame, export_matrix:bool = False):
    pathfinding_map_matrix = map_df.values.tolist()
    grid_export = Grid(matrix=pathfinding_map_matrix)
    if export_matrix:
        return grid_export, pathfinding_map_matrix
    else:
        return grid_export

In [27]:
def find_path(grid: Grid, start_coords: tuple, end_coords: tuple):
    """
    Finds path on a provided grid between two nodes

    :param grid:
    :param start_coords:
    :param end_coords:
    :return: path_res, path_len_res
    """
    start_x, start_y = start_coords
    end_x, end_y = end_coords
    start = grid.node(start_x, start_y)
    end = grid.node(end_x, end_y)
    finder = AStarFinder(diagonal_movement=DiagonalMovement.never)
    path_res, runs = finder.find_path(start, end, grid)
    path_len_res = len(path_res)
    # print('operations:', runs, 'path length:', path_len)
    # print(grid.grid_str(path=path, start=start, end=end))
    grid.cleanup()
    return path_res, path_len_res

In [28]:
def draw_path_to_map(path_to_draw: list, map_to_print: pd.DataFrame):
    path_marker = "🟥"
    print_map = map_to_print.copy()
    # FixMe: if first or last node is above or below the start or finish pop it of because it will otherwise overlap the stop or start
    #path_to_draw.pop(0)
    #path_to_draw.pop(len(path_to_draw)-1)
    for loc in path_to_draw:
        x, y = loc
        print_map.iat[y, x] = path_marker
    return print_map

# Execute pathfinding

In [29]:
debug_coord_s = (5,11)
debug_coord_e = (29,1)
map_pathfinding_grid, map_pathfinding_matrix = instantiate_grid(map_pathfinding, export_matrix=True)

path, path_len = find_path(map_pathfinding_grid, debug_coord_s, debug_coord_e)
display_styled_map(draw_path_to_map(path, map_parcel))


---
# Create district routes

### Split parcel locations into delivery districts

In [30]:
def determine_delivery_district(coords):
    """
    Evaluates provided coordinates to return the delivery district it belongs to
    :param coords:
    :return:
    """
    x, y = coords
    for district, coords_range in delivery_districts.items():
        x_min, y_min = coords_range[0]
        x_max, y_max = coords_range[1]
        if x_min <= x <= x_max and y_min <= y <= y_max:
            return district
    raise ValueError

In [31]:
def evaluate_lots_for_delivery_district():
    """
    Checks which lot with a parcel quantity of > 0 belongs into which delivery district
    """
    for lot, info in master_dict.items():
        if info[key_parcels]>0:
            info[key_delivery_district] = determine_delivery_district(info[key_xy])

In [32]:
evaluate_lots_for_delivery_district()

In [33]:
pprint(master_dict)

{'AAA': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (0, 0)},
 'AAB': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (1, 0)},
 'AAC': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (2, 0)},
 'AAD': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (3, 0)},
 'AAE': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (4, 0)},
 'AAF': {'delivery_district': '',
         'households': 0,
         'lot_use': '.',
         'parcels': 0,
         'path_finding_val': 0,
         'xy': (5, 0)},
 'AAG': {'delive

In [34]:
def split_parcel_locations_into_districts() -> dict:
    """
    Splits all nodes that have parcels into a dict with the delivery district as key.
    :return: {"A":{"AAB":(1,3),"AAD":(4,5)}, "B":{"DAF":(8,4),....}}
    """
    district_quantities = {}
    for district in delivery_districts.keys():
        district_nodes = {}
        district["DEPOT"] =
        for lot, info in master_dict.items():
            if info[key_delivery_district] == district:
                district_nodes[lot] = info[key_xy]
        district_quantities[district] = district_nodes
    return district_quantities

In [35]:
nodes_per_district = split_parcel_locations_into_districts()

In [36]:
pprint(nodes_per_district)

{'A': {'AAJ': (9, 0),
       'AEK': (14, 1),
       'AEL': (15, 1),
       'AES': (22, 1),
       'AHY': (6, 2),
       'AIK': (18, 2),
       'AIS': (26, 2),
       'ALO': (0, 3),
       'APM': (2, 4),
       'APT': (9, 4),
       'APV': (11, 4),
       'AQN': (29, 4),
       'AQP': (31, 4),
       'AQR': (33, 4),
       'AUJ': (29, 5),
       'AXE': (2, 6),
       'AXV': (19, 6),
       'AYB': (25, 6),
       'BAY': (0, 7),
       'BBV': (23, 7),
       'BFD': (9, 8),
       'BFF': (11, 8),
       'BFK': (16, 8),
       'BFT': (25, 8),
       'BFZ': (31, 8),
       'BGA': (32, 8),
       'BIQ': (0, 9),
       'BMO': (2, 10),
       'BMV': (9, 10),
       'BNB': (15, 10),
       'BND': (17, 10),
       'BNF': (19, 10),
       'BNH': (21, 10),
       'BNP': (29, 10),
       'BNR': (31, 10),
       'BQI': (0, 11),
       'BRB': (19, 11),
       'BRD': (21, 11),
       'BRE': (22, 11),
       'BUN': (9, 12),
       'BUZ': (21, 12),
       'BVA': (22, 12),
       'BVL': (33, 12),
       '

### Generate distance matrices within districts

In [75]:
def instantiate_distance_matrices(nodes_in_district: dict, importing_matrices: bool = False) -> dict:
    """
    Creates individual (blank) distance matrices for all delivery districts.
    :param nodes_in_district:
    :param importing_matrices: Flag wether the blank distance matrices will be generated.
    :return: distance_matrices_dict
    {"A": <DF with all lots with parcels in district A>,
    "B": <DF with all lots with parcels in district A>}
    """
    distance_matrices_dict = {}
    if not importing_matrices:
        for district, nodes in nodes_in_district.items():
            lot_names = list(nodes.keys())
            distance_matrix = pd.DataFrame(index=lot_names, columns=lot_names)
            distance_matrices_dict[district] = distance_matrix
    return distance_matrices_dict

In [76]:
def get_remaining_stops(stops: dict, cur_key:str) -> dict:
    """
    Evaluates the remaining nodes which the distance has not been calculated for yet for the current key.
    :param stops:
    :param cur_key:
    :return:
    """
    remaining_stops = {}
    found_key = False
    for key, value in stops.items():
        if key == cur_key:
            found_key = True
        elif found_key:
            remaining_stops[key] = value
    return remaining_stops

In [77]:
def populate_distance_matrix(nodes_in_district: dict, dst_matrix: pd.DataFrame, district: str) -> pd.DataFrame:
    """
    Calculates the distances between each node
    :param dict nodes_in_district: Dict of all lots that will get parcels {'LHU': (38, 76), 'LHZ': (43, 76), 'LIF': (49, 76)}
    :param pd.DataFrame dst_matrix: DF of the instantiated distance matrix
    :param district
    :return:
    """
    for lot_a, node_a in nodes_in_district.items():
        print("------")
        remaining_stops = get_remaining_stops(stops=nodes_in_district, cur_key=lot_a).items()
        remaining_nodes = len(dict(remaining_stops).keys())
        print(f"Remaining nodes: {remaining_nodes}")
        for lot_b, node_b in remaining_stops:
            _, distance = find_path(grid=map_pathfinding_grid,start_coords=node_a,end_coords=node_b)
            print(f"[{district}] Distance from {lot_a}{node_a} to {lot_b}{node_b} = {distance} units")
            dst_matrix.loc[lot_a, lot_b] = distance
            dst_matrix.loc[lot_b, lot_a] = distance

    dst_matrix.fillna(0)  # Fill distance between itself with 0
    return dst_matrix

In [78]:
# Populate distance matrices
if rerun_simulation:
    distance_matrices = instantiate_distance_matrices(nodes_in_district=nodes_per_district, importing_matrices=False)
    for district in delivery_districts.keys():
        print(f"Current district: {district}")
        populate_distance_matrix(nodes_per_district[district], distance_matrices[district], district)
        tmp_df = distance_matrices[district]
        save_df_as_csv(df_to_save=tmp_df, csv_name_no_filetype=f"{csv_distance_matrix_base}{district}")
    pprint(distance_matrices)

    for district in delivery_districts.keys():
        print(f"Saving csv for district {district}")

else:
    distance_matrices = instantiate_distance_matrices(nodes_in_district={}, importing_matrices=True)
    for district in delivery_districts.keys():
        print(f"Retrieving data from csv for district {district}")
        tmp_df = read_df_from_csv(f"{csv_distance_matrix_base}{district}")
        distance_matrices[district] = tmp_df
        del tmp_df
    pprint(distance_matrices)

Current district: A
------
Remaining nodes: 79
[A] Distance from AAJ(9, 0) to AEK(14, 1) = 7 units
[A] Distance from AAJ(9, 0) to AEL(15, 1) = 8 units
[A] Distance from AAJ(9, 0) to AES(22, 1) = 15 units
[A] Distance from AAJ(9, 0) to AHY(6, 2) = 10 units
[A] Distance from AAJ(9, 0) to AIK(18, 2) = 14 units
[A] Distance from AAJ(9, 0) to AIS(26, 2) = 22 units
[A] Distance from AAJ(9, 0) to ALO(0, 3) = 15 units
[A] Distance from AAJ(9, 0) to APM(2, 4) = 14 units
[A] Distance from AAJ(9, 0) to APT(9, 4) = 7 units
[A] Distance from AAJ(9, 0) to APV(11, 4) = 7 units
[A] Distance from AAJ(9, 0) to AQN(29, 4) = 25 units
[A] Distance from AAJ(9, 0) to AQP(31, 4) = 27 units
[A] Distance from AAJ(9, 0) to AQR(33, 4) = 29 units
[A] Distance from AAJ(9, 0) to AUJ(29, 5) = 28 units
[A] Distance from AAJ(9, 0) to AXE(2, 6) = 18 units
[A] Distance from AAJ(9, 0) to AXV(19, 6) = 19 units
[A] Distance from AAJ(9, 0) to AYB(25, 6) = 23 units
[A] Distance from AAJ(9, 0) to BAY(0, 7) = 19 units
[A] Dista

KeyboardInterrupt: 

In [ ]:
display(distance_matrices["A"])